In [6]:
import pandas as pd
import numpy as np
from loaders import *

## PVC

In [7]:
show_config(ConfigRegistry.PVC_ARCH)
show_config(ConfigRegistry.PVC_COMPONENTS_DIR)
result = run_accelergy(ConfigRegistry.PVC_ARCH, ConfigRegistry.PVC_COMPONENTS_DIR)
print(result.ert)

architecture:
  # ============================================================
  # Architecture Description
  # ============================================================
  version: 0.3
  subtree:
    - name: system
      attributes:
        technology: 28nm
        latency: 1ns
      local:
        - name: DRAM
          class: DRAM
          attributes:
            type: LPDDR4
            width: 64
            block-size: 4
            word-bits: 16
      subtree:
        - name: pvc
          local: 
            - name: glb_LBP
              class: SRAM
              attributes:
                technology: 28nm
                datawidth: 16
                depth: 2048
          subtree:
            - name: IPU[0..7]
              attributes:
                meshX: 8
                meshY: 1
              local:
                - name: LBP
                  class: SRAM
                  attributes:
                    technology: 28nm
                    datawidth: 16
            

In [8]:
def parse_stat(layer_stat):
    """
    Total number of compute in this layer
    Number of cycles in this layer
    Energy used in this layer in Joule
    Energy / Compute in picoJoule
    """
    lines = layer_stat.split("\n")
    compute = int(lines[-16].split("=")[-1].strip())
    cycle = int(lines[-21].split(":")[-1].strip())
    energy = float(lines[-20].split(":")[-1].strip()[:-3])
    return compute, cycle, energy * 10**(-6), energy * 10**(-6)  / compute * 10**(12)

### Example layer

In [9]:
example_layer_stats, example_layer_mapping = run_timeloop_mapper(
        ConfigRegistry.PVC_ARCH, ConfigRegistry.PVC_COMPONENTS_DIR,
        ConfigRegistry.PVC_ARCH_CONSTRAINTS,
        ConfigRegistry.PVC_MAP_CONSTRAINTS,
        ConfigRegistry.VGG02_layer5, ConfigRegistry.DEFAULT_MAPPER_SETTING
    )

input file: tmp.yaml
  _______                __                
 /_  __(_)___ ___  ___  / /___  ____  ____ 
  / / / / __ `__ \/ _ \/ / __ \/ __ \/ __ \
 / / / / / / / / /  __/ / /_/ / /_/ / /_/ /
/_/ /_/_/ /_/ /_/\___/_/\____/\____/ .___/ 
                                  /_/      

Problem configuration complete.
execute:/usr/local/bin/accelergy tmp.yaml --oprefix timeloop-mapper. -o ./ > timeloop-mapper.accelergy.log 2>&1
Generate Accelergy ERT (energy reference table) to replace internal energy model.
Generate Accelergy ART (area reference table) to replace internal area model.
Architecture configuration complete.
Sparse optimization configuration complete.
Using threads = 8
Mapper configuration complete.
Initializing Index Factorization subspace.
  Factorization options along problem dimension C = 3432
  Factorization options along problem dimension M = 6435
  Factorization options along problem dimension R = 6
  Factorization options along problem dimension S = 6
  Factorization

[  0] Utilization = 0.02 | pJ/Compute =   92.103 | L4[WIO] Q7 M16 C8 - L3[] C2 Q2X M2X C2X - L2[I] P56 C2 R3X C2X - L1[] Q4 M8 - L0[] S3 
[  0] Utilization = 0.02 | pJ/Compute =   44.373 | L4[WIO] Q7 M16 C8 - L3[] C2 Q2X M2X C2X - L2[I] P56 C2 R3X C2X - L1[W] Q4 M8 - L0[] S3 
[  0] Utilization = 0.02 | pJ/Compute =   41.636 | L4[WIO] Q7 M16 C8 - L3[] C2 Q2X M2X C2X - L2[I] P56 C2 R3X C2X - L1[W] Q4 M8 - L0[I] S3 
[  0] Utilization = 0.02 | pJ/Compute =   40.455 | L4[WIO] Q7 M16 C8 - L3[] C2 Q2X M2X C2X - L2[I] P56 C2 R3X C2X - L1[WI] Q4 M8 - L0[] S3 
[  0] Utilization = 0.02 | pJ/Compute =   32.474 | L4[WIO] Q7 M16 C8 - L3[] C2 Q2X M2X C2X - L2[I] P56 C2 R3X C2X - L1[W] Q4 M8 - L0[O] S3 
[  0] Utilization = 0.02 | pJ/Compute =   29.737 | L4[WIO] Q7 M16 C8 - L3[] C2 Q2X M2X C2X - L2[I] P56 C2 R3X C2X - L1[W] Q4 M8 - L0[IO] S3 
[  1] Utilization = 0.01 | pJ/Compute =  113.436 | L4[WIO] Q7 M16 C8 - L3[] C2 Q2X M2X C2X - L2[I] P56 C4 R3X - L1[] Q4 M8 - L0[] S3 
[  0] Utilization = 0.02 | p

[  2] Utilization = 0.00 | pJ/Compute =   17.027 | L4[WIO] Q7 M2 - L3[] S3 C4 Q4 R3 C2X - L2[I] M8 P56 C2X - L1[W] M2 Q2X - L0[O] M8 C8 
[  1] Utilization = 0.02 | pJ/Compute =  194.359 | L4[WIO] Q7 C4 - L3[] M4 Q2 C2 S3 M2X C2X - L2[I] M4 P56 C2 - L1[] M2 C2 R3 Q2X M4X - L0[] Q2 C2 
[  1] Utilization = 0.02 | pJ/Compute =  163.859 | L4[WIO] Q7 C4 - L3[] M4 Q2 C2 S3 M2X C2X - L2[I] M4 P56 C2 - L1[] M2 C2 R3 Q2X M4X - L0[W] Q2 C2 
[  1] Utilization = 0.02 | pJ/Compute =  162.528 | L4[WIO] Q7 C4 - L3[] M4 Q2 C2 S3 M2X C2X - L2[I] M4 P56 C2 - L1[W] M2 C2 R3 Q2X M4X - L0[] Q2 C2 
[  1] Utilization = 0.02 | pJ/Compute =   79.107 | L4[WIO] Q7 C4 - L3[] M4 Q2 C2 S3 M2X C2X - L2[I] M4 P56 C2 - L1[] M2 C2 R3 Q2X M4X - L0[O] Q2 C2 
[  1] Utilization = 0.02 | pJ/Compute =   48.607 | L4[WIO] Q7 C4 - L3[] M4 Q2 C2 S3 M2X C2X - L2[I] M4 P56 C2 - L1[] M2 C2 R3 Q2X M4X - L0[WO] Q2 C2 
[  1] Utilization = 0.02 | pJ/Compute =   47.276 | L4[WIO] Q7 C4 - L3[] M4 Q2 C2 S3 M2X C2X - L2[I] M4 P56 C2 - L1[W] 

[  2] Utilization = 0.25 | pJ/Compute =    7.402 | L4[WIO] C2 - L3[] R3 C4 Q7 M2 Q2X C4X - L2[I] M4 P56 M16X - L1[WO] M2 S3 Q2 Q2X C2X - L0[] C2 
[  2] Utilization = 0.25 | pJ/Compute =    7.322 | L4[WIO] C2 - L3[] C4 M2 Q7 R3 Q2X C4X - L2[I] M4 P56 M16X - L1[WO] Q2 S3 M2 Q2X C2X - L0[] C2 
[  0] Utilization = 0.06 | pJ/Compute =   24.264 | L4[WIO] M4 - L3[] Q7 C32 R3 Q2X M4X - L2[I] M4 P56 Q2X C2X - L1[WIO] Q2 M2 M2X C2X - L0[] S3 
[  0] Utilization = 0.06 | pJ/Compute =   12.587 | L4[WIO] Q7 C4 - L3[] R3 S3 M16 C8X - L2[I] P56 M2X - L1[W] M2 Q4 Q2X M4X - L0[O] C4 
[  0] Utilization = 0.06 | pJ/Compute =   12.396 | L4[WIO] Q7 C4 - L3[] R3 S3 M16 C8X - L2[I] P56 M2X - L1[WI] M2 Q4 Q2X M4X - L0[O] C4 
[  0] Utilization = 0.06 | pJ/Compute =   10.881 | L4[WIO] Q7 C4 - L3[] R3 S3 M16 C8X - L2[I] P56 M2X - L1[WO] M2 Q4 Q2X M4X - L0[] C4 
[  0] Utilization = 0.06 | pJ/Compute =   10.689 | L4[WIO] Q7 C4 - L3[] R3 S3 M16 C8X - L2[I] P56 M2X - L1[WIO] M2 Q4 Q2X M4X - L0[] C4 
[  5] Utilization

[  4] Utilization = 0.12 | pJ/Compute =    7.105 | L4[WIO] Q7 M2 - L3[] S3 C4 Q2 M2X C4X - L2[I] M2 P56 C8X - L1[WI] Q4 R3 M4X - L0[O] M8 
[  6] Utilization = 0.12 | pJ/Compute =   12.830 | L4[WIO] Q7 C4 - L3[] S3 R3 M16 C8X - L2[I] P56 M2X C2X - L1[W] Q4 M2 Q2X M4X - L0[O] C2 
[  6] Utilization = 0.12 | pJ/Compute =   12.639 | L4[WIO] Q7 C4 - L3[] S3 R3 M16 C8X - L2[I] P56 M2X C2X - L1[WI] Q4 M2 Q2X M4X - L0[O] C2 
[  6] Utilization = 0.12 | pJ/Compute =   10.946 | L4[WIO] Q7 C4 - L3[] S3 R3 M16 C8X - L2[I] P56 M2X C2X - L1[WO] Q4 M2 Q2X M4X - L0[] C2 
[  6] Utilization = 0.12 | pJ/Compute =   10.755 | L4[WIO] Q7 C4 - L3[] S3 R3 M16 C8X - L2[I] P56 M2X C2X - L1[WIO] Q4 M2 Q2X M4X - L0[] C2 
[  4] Utilization = 0.12 | pJ/Compute =    6.922 | L4[WIO] Q7 M2 - L3[] Q2 C4 S3 M2X C4X - L2[I] M2 P56 C8X - L1[WI] Q4 R3 M4X - L0[O] M8 
[  7] STATEMENT: 15000 invalid mappings (14968 fanout, 32 capacity) found since the last valid mapping, terminating search.
[  6] Utilization = 0.12 | pJ/Comput



Summary stats for best mapping found by mapper:
  Utilization = 0.50 | pJ/Compute =    7.204


[  4] STATEMENT: 500 suboptimal mappings found since the last upgrade, terminating search.


In [10]:
parse_stat(example_layer_stats)

(924844032, 903168, 0.00666266, 7.204090386561525)

### Squeeze Nets

In [ ]:
squeeze_layers = ConfigRegistry.SQUEEZE_NET_LAYERS
squeeze_stat = []
for i in range(6, len(squeeze_layers)):
    layer_stats, layer_mapping = run_timeloop_mapper(
        ConfigRegistry.PVC_ARCH, ConfigRegistry.PVC_COMPONENTS_DIR,
        ConfigRegistry.PVC_ARCH_CONSTRAINTS,
        ConfigRegistry.PVC_MAP_CONSTRAINTS,
        squeeze_layers[i+1], ConfigRegistry.DEFAULT_MAPPER_SETTING
    )
    squeeze_stat.append(layer_stats)

In [ ]:
squeeze_stat = []
PATH = 'results/pvc_squeeze_net_results/'
for i in range(1, 27):
    with open(PATH + f'squeeze_result{i}', 'r') as file:
        squeeze_stat.append(file.read())

squeeze_total_compute = 0
squeeze_total_cycle = 0
squeeze_total_energy = 0

for stat in squeeze_stat:
    compute, cycle, energy, energy_per_compute = parse_stat(stat)
    squeeze_total_compute += compute
    squeeze_total_cycle += cycle
    squeeze_total_energy += energy

print(f"Squeeze Net Total Compute:", squeeze_total_compute)
print(f"Squeeze Net Total Cycle:", squeeze_total_cycle)
print(f"Squeeze Net Total Energy:", squeeze_total_energy)
print(f"Squeeze Net Energy / Computer pJ / Compute", squeeze_total_energy / squeeze_total_compute * 10 ** (12))

In [ ]:
for i in range(6, len(squeeze_stat)+6):
    text_file = open(f"squeeze_result{i+1}", "w")
    text_file.write(squeeze_stat[i-6])
    text_file.close()

In [ ]:
print(len(squeeze_stat))

### Mobile Nets

In [ ]:
mobile_layers = ConfigRegistry.MOBILE_NET_LAYERS
mobile_stat = []
for i in range(len(mobile_layers)):
    layer_stats, layer_mapping = run_timeloop_mapper(
        ConfigRegistry.PVC_ARCH, ConfigRegistry.PVC_COMPONENTS_DIR,
        ConfigRegistry.PVC_ARCH_CONSTRAINTS,
        ConfigRegistry.PVC_MAP_CONSTRAINTS,
        mobile_layers[i+1], ConfigRegistry.DEFAULT_MAPPER_SETTING
    )
    mobile_stat.append(layer_stats)

In [ ]:
mobile_total_compute = 0
mobile_total_cycle = 0
mobile_total_energy = 0

for stat in mobile_stat:
    try:
        compute, cycle, energy, energy_per_compute = parse_stat(stat)
        mobile_total_compute += compute
        mobile_total_cycle += cycle
        mobile_total_energy += energy
    except:
        continue

print(f"Mobile Net Total Compute:", mobile_total_compute)
print(f"Mobile Net Total Cycle:", mobile_total_cycle)
print(f"Mobile Net Total Energy:", mobile_total_energy)
print(f"Mobile Net Energy / Computer pJ / Compute", mobile_total_energy / mobile_total_compute * 10 ** (12))

In [ ]:
for i in range(len(mobile_stat)):
    text_file = open(f"mobile_result{i+1}", "w")
    text_file.write(mobile_stat[i])
    text_file.close()

### Dense Net

In [11]:
dense_layers = ConfigRegistry.DENSE_NET_LAYERS 
dense_stat = []
for i in range(len(dense_layers)):
    layer_stats, layer_mapping = run_timeloop_mapper(
        ConfigRegistry.PVC_ARCH, ConfigRegistry.PVC_COMPONENTS_DIR,
        ConfigRegistry.PVC_ARCH_CONSTRAINTS,
        ConfigRegistry.PVC_MAP_CONSTRAINTS,
        dense_layers[i+1], ConfigRegistry.DEFAULT_MAPPER_SETTING
    )
    dense_stat.append(layer_stats)

input file: tmp.yaml
  _______                __                
 /_  __(_)___ ___  ___  / /___  ____  ____ 
  / / / / __ `__ \/ _ \/ / __ \/ __ \/ __ \
 / / / / / / / / /  __/ / /_/ / /_/ / /_/ /
/_/ /_/_/ /_/ /_/\___/_/\____/\____/ .___/ 
                                  /_/      

Problem configuration complete.
execute:/usr/local/bin/accelergy tmp.yaml --oprefix timeloop-mapper. -o ./ > timeloop-mapper.accelergy.log 2>&1
Generate Accelergy ERT (energy reference table) to replace internal energy model.
Generate Accelergy ART (area reference table) to replace internal area model.
Architecture configuration complete.
Sparse optimization configuration complete.
Using threads = 8
Mapper configuration complete.
Initializing Index Factorization subspace.
  Factorization options along problem dimension C = 8
  Factorization options along problem dimension M = 1716
  Factorization options along problem dimension R = 6
  Factorization options along problem dimension S = 6
  Factorization op

[  3] Utilization = 0.01 | pJ/Compute =  168.094 | L4[WIO] Q2 M4 - L3[] R7 Q28 S7 Q2X - L2[I] P112 M2X C3X - L1[] Q1 - L0[] M8 
[  3] Utilization = 0.01 | pJ/Compute =  105.674 | L4[WIO] Q2 M4 - L3[] R7 Q28 S7 Q2X - L2[I] P112 M2X C3X - L1[] Q1 - L0[W] M8 
[  3] Utilization = 0.01 | pJ/Compute =  104.871 | L4[WIO] Q2 M4 - L3[] R7 Q28 S7 Q2X - L2[I] P112 M2X C3X - L1[W] Q1 - L0[] M8 
[  3] Utilization = 0.01 | pJ/Compute =  104.065 | L4[WIO] Q2 M4 - L3[] R7 Q28 S7 Q2X - L2[I] P112 M2X C3X - L1[W] Q1 - L0[I] M8 
[  3] Utilization = 0.01 | pJ/Compute =  103.177 | L4[WIO] Q2 M4 - L3[] R7 Q28 S7 Q2X - L2[I] P112 M2X C3X - L1[WI] Q1 - L0[] M8 
[  1] Utilization = 0.01 | pJ/Compute =  168.094 | L4[WIO] Q2 M4 - L3[] S7 R7 Q28 Q2X - L2[I] P112 M2X - L1[] Q1 C3X - L0[] M8 
[  1] Utilization = 0.01 | pJ/Compute =  105.115 | L4[WIO] Q2 M4 - L3[] S7 R7 Q28 Q2X - L2[I] P112 M2X - L1[] Q1 C3X - L0[W] M8 
[  5] Utilization = 0.01 | pJ/Compute =  154.079 | L4[WIO] Q2 M4 - L3[] Q28 S7 R7 Q2X C3X - L2[I]

[  2] Utilization = 0.00 | pJ/Compute =   93.183 | L4[WIO] Q2 M4 - L3[] S7 Q28 R7 Q2X - L2[I] P112 M2X - L1[W] C3 - L0[O] M8 
[  2] Utilization = 0.00 | pJ/Compute =   92.377 | L4[WIO] Q2 M4 - L3[] S7 Q28 R7 Q2X - L2[I] P112 M2X - L1[W] C3 - L0[IO] M8 
[  2] Utilization = 0.00 | pJ/Compute =   91.489 | L4[WIO] Q2 M4 - L3[] S7 Q28 R7 Q2X - L2[I] P112 M2X - L1[WI] C3 - L0[O] M8 
[  2] Utilization = 0.00 | pJ/Compute =   90.609 | L4[WIO] Q2 M4 - L3[] S7 Q28 R7 Q2X - L2[I] P112 M2X - L1[WO] C3 - L0[I] M8 
[  2] Utilization = 0.00 | pJ/Compute =   89.721 | L4[WIO] Q2 M4 - L3[] S7 Q28 R7 Q2X - L2[I] P112 M2X - L1[WIO] C3 - L0[] M8 
[  0] Utilization = 0.02 | pJ/Compute =  138.370 | L4[WIO] Q112 M4 - L3[] Q1 S7X - L2[I] M16 P112 R7X - L1[] Q1 - L0[] C3 
[  0] Utilization = 0.02 | pJ/Compute =   12.522 | L4[WIO] Q112 M4 - L3[] Q1 S7X - L2[I] M16 P112 R7X - L1[] Q1 - L0[W] C3 
[  0] Utilization = 0.02 | pJ/Compute =   11.719 | L4[WIO] Q112 M4 - L3[] Q1 S7X - L2[I] M16 P112 R7X - L1[W] Q1 - L0[]

[  2] Utilization = 0.05 | pJ/Compute =  275.896 | L4[WIO] M2 - L3[] S7 Q16 Q7X - L2[I] P112 M8X - L1[] R7 C3 M2 M2X - L0[] Q1 
[  2] Utilization = 0.05 | pJ/Compute =  257.824 | L4[WIO] M2 - L3[] S7 Q16 Q7X - L2[I] P112 M8X - L1[W] R7 C3 M2 M2X - L0[] Q1 
[  2] Utilization = 0.05 | pJ/Compute =   32.569 | L4[WIO] M2 - L3[] S7 Q16 Q7X - L2[I] P112 M8X - L1[O] R7 C3 M2 M2X - L0[] Q1 
[  2] Utilization = 0.05 | pJ/Compute =   14.497 | L4[WIO] M2 - L3[] S7 Q16 Q7X - L2[I] P112 M8X - L1[WO] R7 C3 M2 M2X - L0[] Q1 
[  2] Utilization = 0.05 | pJ/Compute =   14.382 | L4[WIO] M2 - L3[] S7 Q16 Q7X - L2[I] P112 M8X - L1[WIO] R7 C3 M2 M2X - L0[] Q1 
[  0] Utilization = 0.05 | pJ/Compute =   14.497 | L4[WIO] M2 - L3[] S7 Q16 Q7X - L2[I] P112 M8X - L1[WO] R7 M2 M2X - L0[] C3 
[  0] Utilization = 0.05 | pJ/Compute =   14.382 | L4[WIO] M2 - L3[] S7 Q16 Q7X - L2[I] P112 M8X - L1[WIO] R7 M2 M2X - L0[] C3 
[  6] Utilization = 0.05 | pJ/Compute =   74.370 | L4[WIO] Q1 - L3[] Q56 C3 Q2X - L2[I] P112 S7X -

[  7] STATEMENT: 500 suboptimal mappings found since the last upgrade, terminating search.
[  5] STATEMENT: 500 suboptimal mappings found since the last upgrade, terminating search.


...

[  4] Utilization = 0.04 | pJ/Compute =  162.030 | L4[WIO] M2 - L3[] C4 M2X C2X - L2[I] M5 C4 M5X C4X - L1[] C8 M10 - L0[] Q1 
[  4] Utilization = 0.04 | pJ/Compute =  161.465 | L4[WIO] M2 - L3[] C4 M2X C2X - L2[I] M5 C4 M5X C4X - L1[I] C8 M10 - L0[] Q1 
[  0] Utilization = 0.08 | pJ/Compute =  130.240 | L4[WIO] M2 - L3[O] C4 M2X C2X - L2[I] M5 C4 M5X C4X - L1[I] M10 C2 C2X - L0[] C2 
[  4] Utilization = 0.04 | pJ/Compute =  131.508 | L4[WIO] M2 - L3[] C4 M2X C2X - L2[I] M5 C4 M5X C4X - L1[O] C8 M10 - L0[] Q1 
[  4] Utilization = 0.04 | pJ/Compute =  130.943 | L4[WIO] M2 - L3[] C4 M2X C2X - L2[I] M5 C4 M5X C4X - L1[IO] C8 M10 - L0[] Q1 
[  0] Utilization = 0.08 | pJ/Compute =  129.990 | L4[WIO] M2 - L3[O] C4 M2X C2X - L2[I] M5 C4 M5X C4X - L1[IO] M10 C2 C2X - L0[] C2 
[  4] Utilization = 0.04 | pJ/Compute =  130.765 | L4[WIO] M2 - L3[O] C4 M2X C2X - L2[I] M5 C4 M5X C4X - L1[I] C8 M10 - L0[] Q1 
[  4] Utilization = 0.04 | pJ/Compute =  130.226 | L4[WIO] M2 - L3[O] C4 M2X C2X - L2[I] M5 

[  7] Utilization = 0.24 | pJ/Compute =  129.956 | L4[WIO] Q1 - L3[O] C4 M2 M5X - L2[I] Q1 M5X C4X - L1[O] C32 M4 M5X - L0[] C2 
[  3] Utilization = 0.16 | pJ/Compute =  145.452 | L4[WIO] C4 - L3[] C4 M2X C4X - L2[I] Q1 M5X - L1[] C2 M2X C4X - L0[] M50 C2 
[  3] Utilization = 0.16 | pJ/Compute =  145.124 | L4[WIO] C4 - L3[] C4 M2X C4X - L2[I] Q1 M5X - L1[I] C2 M2X C4X - L0[] M50 C2 
[  3] Utilization = 0.16 | pJ/Compute =  129.820 | L4[WIO] C4 - L3[] C4 M2X C4X - L2[I] Q1 M5X - L1[O] C2 M2X C4X - L0[] M50 C2 
[  3] Utilization = 0.16 | pJ/Compute =  129.492 | L4[WIO] C4 - L3[] C4 M2X C4X - L2[I] Q1 M5X - L1[IO] C2 M2X C4X - L0[] M50 C2 
[  2] Utilization = 0.10 | pJ/Compute =  193.464 | L4[WIO] C128 - L3[] M10 M5X - L2[I] Q1 M5X - L1[] M2 M2X C4X - L0[] C2 
[  2] Utilization = 0.10 | pJ/Compute =  193.153 | L4[WIO] C128 - L3[] M10 M5X - L2[I] Q1 M5X - L1[I] M2 M2X C4X - L0[] C2 
[  2] Utilization = 0.10 | pJ/Compute =  163.960 | L4[WIO] C128 - L3[] M10 M5X - L2[I] Q1 M5X - L1[] M2 M2X 

[  1] STATEMENT: 500 suboptimal mappings found since the last upgrade, terminating search.
[  4] Utilization = 0.62 | pJ/Compute =  137.460 | L4[WIO] C4 - L3[] C4 M4X C2X - L2[I] M5 M5X C4X - L1[] M5 M2X C4X - L0[] C2 
[  4] Utilization = 0.62 | pJ/Compute =  137.144 | L4[WIO] C4 - L3[] C4 M4X C2X - L2[I] M5 M5X C4X - L1[I] M5 M2X C4X - L0[] C2 
[  4] Utilization = 0.62 | pJ/Compute =  135.929 | L4[WIO] C4 - L3[] C4 M4X C2X - L2[I] M5 M5X C4X - L1[] M5 M2X C4X - L0[O] C2 
[  4] Utilization = 0.62 | pJ/Compute =  135.612 | L4[WIO] C4 - L3[] C4 M4X C2X - L2[I] M5 M5X C4X - L1[I] M5 M2X C4X - L0[O] C2 
[  4] Utilization = 0.62 | pJ/Compute =  133.610 | L4[WIO] C4 - L3[] C4 M4X C2X - L2[I] M5 M5X C4X - L1[O] M5 M2X C4X - L0[] C2 
[  4] Utilization = 0.62 | pJ/Compute =  133.293 | L4[WIO] C4 - L3[] C4 M4X C2X - L2[I] M5 M5X C4X - L1[IO] M5 M2X C4X - L0[] C2 
[  4] Utilization = 0.62 | pJ/Compute =  129.972 | L4[WIO] C4 - L3[O] C4 M4X C2X - L2[I] M5 M5X C4X - L1[] M5 M2X C4X - L0[] C2 
[  4]



Summary stats for best mapping found by mapper:
  Utilization = 0.62 | pJ/Compute =  129.656


[  5] STATEMENT: 500 suboptimal mappings found since the last upgrade, terminating search.


In [12]:
dense_total_compute = 0
dense_total_cycle = 0
dense_total_energy = 0

for stat in dense_stat:
    compute, cycle, energy, energy_per_compute = parse_stat(stat)
    dense_total_compute += compute
    dense_total_cycle += cycle
    dense_total_energy += energy

print(f"Dense Net Total Compute:", dense_total_compute)
print(f"Dense Net Total Cycle:", dense_total_cycle)
print(f"Dense Net Total Energy:", dense_total_energy)
print(f"Dense Net Energy / Computer pJ / Compute", dense_total_energy / dense_total_compute * 10 ** (12))

Dense Net Total Compute: 2834161664
Dense Net Total Cycle: 2748580
Dense Net Total Energy: 0.05445127999999999
Dense Net Energy / Computer pJ / Compute 19.21248201598707


In [13]:
for i in range(len(dense_stat)):
    text_file = open(f"dense_result{i+1}", "w")
    text_file.write(dense_stat[i])
    text_file.close()